# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

* [Introduction: Business Problem](#introduction)

* [Data](#data)

* [Methodology](#methodology)

* [Analysis](#analysis)

* [Results and Discussion](#results)

* [Conclusion](#conclusion)

    </font>
    </div>

## 1. Introduction: Business Problem <a name="introduction"></a>

In this project we will try to compare the neighborhood cities of a particular state in the US i.e. how similar & dissimilar they are. Specifically, this report will be targeted to stakeholders interested in opening different types of businesses as they see fit in any particular city of US.

Since there are lots of businesses in US we will try to detect **top businesses in any particular city**. We are also particularly interested in **a certain business which is not so popular in a particular city**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promising neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## 2. Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of any particular existing business in the city.
* distance of neighborhood from city center.

Following data sources will be needed to extract/generate the required information:
* list of cities in all of the states in the US obtained from webscraping of Britannica website and then forming it into a dataframe(.csv file)
* number of businesses and their type and location in every neighborhood city will be obtained using **Foursquare API**

#### Before we get the data and start exploring it, let's import all the dependencies that we will need.

In [1]:
import pandas as pd # for data processing
import numpy as np # library to handle data in a vectorized manner
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
import folium   #for creating maps
import requests  #for retreiving Information from URL

import geocoder
from geopy.geocoders import Nominatim  #converting address to cordinates
from pandas.io.json import json_normalize #converting json to DataFrame

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

print('Libraries imported.')

Libraries imported.


#### Getting the dataframe of all the US states and its cities. (Source:Britannica) (Already Webscrapped and converted into a CSV file for efficient execution)

In [2]:
df1_usa = pd.read_csv('file1.csv')
df1_usa.head()

Alabama     Alaska      Arizona       Arkansas California  \
0  Alexander City  Anchorage          Ajo    Arkadelphia    Alameda   
1       Andalusia    Cordova     Avondale  Arkansas Post   Alhambra   
2        Anniston  Fairbanks       Bisbee     Batesville    Anaheim   
3          Athens     Haines  Casa Grande         Benton    Antioch   
4          Atmore      Homer     Chandler    Blytheville    Arcadia   

       Colorado Connecticut    Delaware       Florida        Georgia  \
0       Alamosa     Ansonia       Dover  Apalachicola         Albany   
1         Aspen      Berlin       Lewes        Bartow       Americus   
2        Aurora  Bloomfield     Milford   Belle Glade  Andersonville   
3       Boulder    Branford  New Castle    Boca Raton         Athens   
4  Breckenridge  Bridgeport      Newark     Bradenton        Atlanta   

     Hawaii          Idaho           Illinois       Indiana            Iowa  \
0   Hanalei      Blackfoot              Alton      Anderson  Amana Colonies   
1      Hilo          Boise  Arlington Heights       Bedford            Ames   
2  Honaunau  Bonners Ferry             Arthur   Bloomington           Boone   
3  Honolulu       Caldwell             Aurora      Columbus      Burlington   
4   Kahului  Coeur d’Alene         Belleville  Connersville     Cedar Falls   

          Kansas       Kentucky    Louisiana       Maine  \
0        Abilene        Ashland    Abbeville      Auburn   
1  Arkansas City   Barbourville   Alexandria     Augusta   
2       Atchison      Bardstown      Bastrop      Bangor   
3        Chanute          Berea  Baton Rouge  Bar Harbor   
4    Coffeyville  Boonesborough     Bogalusa        Bath   

               Maryland Massachusetts      Michigan    Minnesota  \
0              Aberdeen      Abington        Adrian   Albert Lea   
1             Annapolis         Adams          Alma   Alexandria   
2             Baltimore      Amesbury     Ann Arbor       Austin   
3  Bethesda-Chevy Chase       Amherst  Battle Creek      Bemidji   
4                 Bowie       Andover      Bay City  Bloomington   

       Mississippi        Missouri   Montana   Nebraska        Nevada  \
0  Bay Saint Louis       Boonville  Anaconda   Beatrice  Boulder City   
1           Biloxi         Branson  Billings   Bellevue   Carson City   
2           Canton  Cape Girardeau   Bozeman  Boys Town          Elko   
3       Clarksdale        Carthage     Butte    Chadron           Ely   
4         Columbia     Chillicothe    Dillon   Columbus        Fallon   

  New Hampshire     New Jersey   New Mexico   New York North Carolina  \
0        Berlin    Asbury Park        Acoma     Albany       Asheboro   
1     Claremont  Atlantic City   Alamogordo  Amsterdam      Asheville   
2       Concord        Bayonne  Albuquerque     Auburn           Bath   
3         Derry     Bloomfield      Artesia    Babylon       Beaufort   
4         Dover     Bordentown        Belen    Batavia          Boone   

  North Dakota       Ohio  Oklahoma      Oregon Pennsylvania    Rhode Island  \
0     Bismarck      Akron       Ada      Albany     Abington      Barrington   
1  Devils Lake   Alliance     Altus     Ashland    Aliquippa         Bristol   
2    Dickinson  Ashtabula      Alva     Astoria    Allentown   Central Falls   
3        Fargo     Athens  Anadarko  Baker City      Altoona        Cranston   
4  Grand Forks  Barberton   Ardmore   Beaverton     Ambridge  East Greenwich   

  South Carolina   South Dakota    Tennessee      Texas           Utah  \
0      Abbeville       Aberdeen        Alcoa    Abilene           Alta   
1          Aiken  Belle Fourche       Athens     Alpine  American Fork   
2       Anderson      Brookings  Chattanooga   Amarillo      Bountiful   
3       Beaufort         Canton  Clarksville  Arlington   Brigham City   
4         Camden         Custer    Cleveland     Austin     Cedar City   

         Vermont         Virginia  Washington West Virginia Wisconsin  \
0          Barre         Abi

#### Selecting a state below from the list of 50 states in the above dataframe.

In [3]:
col_list= ["Alabama"]
x = 'Alabama'
state_data = pd.read_csv("file1.csv", usecols=col_list)
temp_df = state_data
temp1_df = temp_df.rename(columns={x: "Neighborhood"})
state_df= temp1_df.dropna()
state_df

Neighborhood
0   Alexander City
1        Andalusia
2         Anniston
3           Athens
4           Atmore
5           Auburn
6         Bessemer
7       Birmingham
8        Chickasaw
9          Clanton
10         Cullman
11         Decatur
12       Demopolis
13          Dothan
14      Enterprise
15         Eufaula
16        Florence
17      Fort Payne
18         Gadsden
19      Greenville
20    Guntersville
21      Huntsville
22          Jasper
23          Marion
24          Mobile
25      Montgomery
26         Opelika
27           Ozark
28     Phenix City
29        Prichard
30      Scottsboro
31           Selma
32       Sheffield
33       Sylacauga
34       Talladega
35            Troy
36      Tuscaloosa
37       Tuscumbia
38        Tuskegee

#### Get the geographical coordinates of all the neighboring cities of that state.

In [4]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, {}, USA'.format(neighborhood, x)) #Here x is the state you entered.
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [5]:
coords = [ get_latlng(neighborhood) for neighborhood in state_df["Neighborhood"].tolist() ]
coords

[[32.93884000000003, -85.95294999999999],
 [31.320140000000038, -86.49448999999998],
 [33.65712000000008, -85.81890999999996],
 [34.804500000000075, -86.97127999999998],
 [31.02526000000006, -87.49379999999996],
 [32.60829000000007, -85.48172999999997],
 [33.402030000000025, -86.95398999999998],
 [33.52068000000003, -86.81175999999994],
 [30.76461000000006, -88.07475999999997],
 [32.840850000000046, -86.63201999999995],
 [34.17437000000007, -86.84344999999996],
 [34.60740000000004, -86.97978999999998],
 [32.50475000000006, -87.83780999999999],
 [31.223250000000064, -85.39336999999995],
 [31.315150000000074, -85.85461999999995],
 [31.894980000000032, -85.14584999999994],
 [34.80060000000003, -87.67488999999995],
 [34.441310000000044, -85.71436999999997],
 [34.014770000000055, -86.00716999999997],
 [31.829440000000034, -86.63360999999998],
 [34.35143000000005, -86.29893999999996],
 [34.72929000000005, -86.58509999999995],
 [33.83128000000005, -87.28084999999999],
 [32.63467000000003, -87

In [6]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

#### Convert it into a dataframe and quickly examine the resulting dataframe.

In [7]:
# merge the coordinates into the original dataframe
state_df['Latitude'] = df_coords['Latitude']
state_df['Longitude'] = df_coords['Longitude']
print(state_df.shape)
state_df

(39, 3)
<ipython-input-7-4d02ce365442>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  state_df['Latitude'] = df_coords['Latitude']
<ipython-input-7-4d02ce365442>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  state_df['Longitude'] = df_coords['Longitude']


Neighborhood  Latitude  Longitude
0   Alexander City  32.93884  -85.95295
1        Andalusia  31.32014  -86.49449
2         Anniston  33.65712  -85.81891
3           Athens  34.80450  -86.97128
4           Atmore  31.02526  -87.49380
5           Auburn  32.60829  -85.48173
6         Bessemer  33.40203  -86.95399
7       Birmingham  33.52068  -86.81176
8        Chickasaw  30.76461  -88.07476
9          Clanton  32.84085  -86.63202
10         Cullman  34.17437  -86.84345
11         Decatur  34.60740  -86.97979
12       Demopolis  32.50475  -87.83781
13          Dothan  31.22325  -85.39337
14      Enterprise  31.31515  -85.85462
15         Eufaula  31.89498  -85.14585
16        Florence  34.80060  -87.67489
17      Fort Payne  34.44131  -85.71437
18         Gadsden  34.01477  -86.00717
19      Greenville  31.82944  -86.63361
20    Guntersville  34.35143  -86.29894
21      Huntsville  34.72929  -86.58510
22          Jasper  33.83128  -87.28085
23          Marion  32.63467  -87.31913
24          Mobile  30.68648  -88.05297
25      Montgomery  32.38015  -86.30008
26         Opelika  32.65050  -85.38065
27           Ozark  31.45895  -85.64071
28     Phenix City  32.46809  -85.00083
29        Prichard  30.73799  -88.08127
30      Scottsboro  34.68520  -86.09461
31           Selma  32.41279  -87.02282
32       Sheffield  34.75961  -87.68715
33       Sylacauga  33.17156  -86.25025
34       Talladega  33.43451  -86.10269
35            Troy  31.80967  -85.97217
36      Tuscaloosa  33.21042  -87.56625
37       Tuscumbia  34.73136  -87.70287
38        Tuskegee  32.42405  -85.68978

#### Use geopy library to get the latitude and longitude values of the selected state.

In [8]:
# get the coordinates of the state
address = '{}, USA'.format(x)

geolocator = Nominatim(user_agent="x_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {}, USA {}, {}.'.format(x, latitude, longitude))

The geograpical coordinate of Alabama, USA 33.2588817, -86.8295337.


#### Creating a map of the selected state with neighboring cities superimposed on top.

In [9]:
# create map of Toronto using latitude and longitude values
map_x = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to map
for lat, lng, neighborhood in zip(state_df['Latitude'], state_df['Longitude'], state_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='purple',
        fill=True,
        fill_color='#6600cc',
        fill_opacity=0.7).add_to(map_x)  
    
map_x

#### Define your Foursquare Credentials.

In [10]:
CLIENT_ID = 'I1EWMQ1R1WILTIR2QLXNWSL5FTED2B2LSKBXBZIPKWZCWPPJ' # replace it with your Client id
CLIENT_SECRET = 'YF0LMXIW1I0C0E1BPY0FEMZPPDBYUPKQW5NHOUPHYE52G52D' # replace it with your client secret
VERSION = '20180605' # Foursquare API version

#### Now, lets get the top 1400 venues that are within a radius of 15 KMs or 9.3 Miles.

In [11]:
radius = 15000  #You can change these according to your preferences.
LIMIT = 1400

venues = []

for lat, long, neighborhood in zip(state_df['Latitude'], state_df['Longitude'], state_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['distance'], 
            venue['venue']['location']['lat'],  
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [12]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'Distance', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head(50)

(2700, 8)


Neighborhood  Latitude  Longitude  \
0   Alexander City  32.93884  -85.95295   
1   Alexander City  32.93884  -85.95295   
2   Alexander City  32.93884  -85.95295   
3   Alexander City  32.93884  -85.95295   
4   Alexander City  32.93884  -85.95295   
5   Alexander City  32.93884  -85.95295   
6   Alexander City  32.93884  -85.95295   
7   Alexander City  32.93884  -85.95295   
8   Alexander City  32.93884  -85.95295   
9   Alexander City  32.93884  -85.95295   
10  Alexander City  32.93884  -85.95295   
11  Alexander City  32.93884  -85.95295   
12  Alexander City  32.93884  -85.95295   
13  Alexander City  32.93884  -85.95295   
14  Alexander City  32.93884  -85.95295   
15  Alexander City  32.93884  -85.95295   
16  Alexander City  32.93884  -85.95295   
17  Alexander City  32.93884  -85.95295   
18  Alexander City  32.93884  -85.95295   
19  Alexander City  32.93884  -85.95295   
20  Alexander City  32.93884  -85.95295   
21  Alexander City  32.93884  -85.95295   
22  Alexander City  32.93884  -85.95295   
23  Alexander City  32.93884  -85.95295   
24  Alexander City  32.93884  -85.95295   
25  Alexander City  32.93884  -85.95295   
26  Alexander City  32.93884  -85.95295   
27  Alexander City  32.93884  -85.95295   
28  Alexander City  32.93884  -85.95295   
29  Alexander City  32.93884  -85.95295   
30  Alexander City  32.93884  -85.95295   
31  Alexander City  32.93884  -85.95295   
32  Alexander City  32.93884  -85.95295   
33  Alexander City  32.93884  -85.95295   
34  Alexander City  32.93884  -85.95295   
35  Alexander City  32.93884  -85.95295   
36  Alexander City  32.93884  -85.95295   
37  Alexander City  32.93884  -85.95295   
38       Andalusia  31.32014  -86.49449   
39       Andalusia  31.32014  -86.49449   
40       Andalusia  31.32014  -86.49449   
41       Andalusia  31.32014  -86.49449   
42       Andalusia  31.32014  -86.49449   
43       Andalusia  31.32014  -86.49449   
44       Andalusia  31.32014  -86.49449   
45       Andalusia  31.32014  -86.49449   
46       Andalusia  31.32014  -86.49449   
47       Andalusia  31.32014  -86.49449   
48       Andalusia  31.32014  -86.49449   
49       Andalusia  31.32014  -86.49449   

                                  VenueName  Distance  VenueLatitude  \
0                   JR's Sports Bar & Grill       607      32.944276   
1                   La Posada Mexican Grill      1729      32.926987   
2                              Ruby Tuesday      1786      32.923797   
3          Wind Creek State Park Campground      9625      32.855093   
4                                MAPCO Mart      2509      32.916299   
5                           Anytime Fitness       717      32.945230   
6                            Dollar General       961      32.931278   
7                     Wind Creek State Park      9541      32.856710   
8                                 Jim Bob's      1090      32.929910   
9                                    Subway      2193      32.919853   
10                Dairy Queen Grill & Chill      1726      32.933872   
11                             Sho Nuff BBQ       950      32.931937   
12                              Dollar Tree      2119      32.920815   
13                                   Arby's      2269      32.939407   
14                            Piggly Wiggly       813      32.946138   
15  Zaxby's Chicken Fingers & Buffalo Wings      2196      32.919178   
16                                Pizza Hut      2280      32.918390   
17                             Huddle House      2457      32.916762   
18                               Winn-Dixie      1982      32.922303   
19                              Captain D's      1892      32.923259   
20                     Little Caesars Pizza      1875      32.935593   
21                               Murphy USA      2359      32.940234   
22                                 Rite Aid      2150      32.919633   
23                                 Hardee's      1011      32.930829   
24          

### Moving on to the number of venues that were returned for neighboring cities.

In [13]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 218 uniques categories.


#### Sorting & assigning each venue category a unique venue number.

In [14]:
sortedvenues = venues_df.sort_values('VenueCategory')
sortedvenues['VenueNumber']=sortedvenues.groupby(['VenueCategory']).ngroup()
sortedvenues.head()

Neighborhood  Latitude  Longitude                    VenueName  Distance  \
96       Anniston  33.65712  -85.81891       Bama Fever Tiger Pride      6358   
1974        Ozark  31.45895  -85.64071              Hunt Stagefield     10732   
874     Demopolis  32.50475  -87.83781  Demopolis Municipal Airport     11802   
1975        Ozark  31.45895  -85.64071                    Molinelli     13814   
1062   Enterprise  31.31515  -85.85462         Cairns Army Airfield     13333   

      VenueLatitude  VenueLongitude      VenueCategory  VenueNumber  
96        33.607930      -85.784037  Accessories Store            0  
1974      31.377644      -85.579995            Airport            1  
874       32.462050      -87.952852            Airport            1  
1975      31.481746      -85.783731            Airport            1  
1062      31.282587      -85.719722            Airport            1

### Creating a map for visualizing all the different venues in different cities with there unique venue number & colour i.e. how each city is different from each other for the particular selected state.

In [18]:
# create map
map_k = folium.Map(location=[latitude, longitude], zoom_start=7)

# set color scheme for the clusters
vlength = len(venues_df['VenueCategory'].unique())
x = np.arange(vlength)
ys = [i + x + (i*x)**2 for i in range(vlength)]
colors_array = iter(cm.rainbow(np.linspace(0, 1, len(ys))))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []

for lat, lon, cate, nos, city in zip(sortedvenues.VenueLatitude, sortedvenues.VenueLongitude, sortedvenues.VenueCategory, sortedvenues.VenueNumber, sortedvenues.Neighborhood):
    label = 'Category:{}, Category No.:{}, City:{}'.format(cate, nos, city)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[nos-1],
        fill=True,
        fill_opacity=1,
        fill_color=rainbow[nos-1]).add_to(map_k)
       
map_k

### You can also select a particular city for seeing the top venues around the neighborhood.

In [17]:
y = 'Birmingham'
x_data = venues_df[venues_df['Neighborhood'] == y].reset_index(drop=True)
x_data.head()

Neighborhood  Latitude  Longitude                          VenueName  \
0   Birmingham  33.52068  -86.81176           Birmingham Museum Of Art   
1   Birmingham  33.52068  -86.81176                          El Barrio   
2   Birmingham  33.52068  -86.81176  Birmingham Civil Rights Institute   
3   Birmingham  33.52068  -86.81176              McWane Science Center   
4   Birmingham  33.52068  -86.81176                    The Collins Bar   

   Distance  VenueLatitude  VenueLongitude       VenueCategory  
0       220      33.522311      -86.810409          Art Museum  
1       910      33.516913      -86.803053  Mexican Restaurant  
2       574      33.516083      -86.814564      History Museum  
3       668      33.515297      -86.808559      Science Museum  
4       869      33.516507      -86.803835                 Bar

### Moving on to the number of venues that were returned for the selected city.

In [35]:
print('There are {} uniques categories.'.format(len(x_data['VenueCategory'].unique())))

There are 59 uniques categories.


#### Sorting & assigning each venue category a unique venue number.

In [18]:
sortedx = x_data.sort_values('VenueCategory')
sortedx['VenueNumber']=sortedx.groupby(['VenueCategory']).ngroup()
sortedx.head()

Neighborhood  Latitude  Longitude                         VenueName  \
66   Birmingham  33.52068  -86.81176               Newk's Express Cafe   
46   Birmingham  33.52068  -86.81176                   Galley & Garden   
50   Birmingham  33.52068  -86.81176  Jack Brown's Beer & Burger Joint   
22   Birmingham  33.52068  -86.81176                      Pies & Pints   
0    Birmingham  33.52068  -86.81176          Birmingham Museum Of Art   

    Distance  VenueLatitude  VenueLongitude        VenueCategory  VenueNumber  
66      1910      33.507419      -86.798701  American Restaurant            0  
46      2924      33.501173      -86.790663  American Restaurant            0  
50      2410      33.511413      -86.788280  American Restaurant            0  
22      1326      33.511170      -86.803148  American Restaurant            0  
0        220      33.522311      -86.810409           Art Museum            1

#### Let's get the geographical coordinates of your selected city.

In [26]:
lati = sortedx.Latitude[0]
lng = sortedx.Longitude[0]
print('The geograpical coordinate of {} are {}, {}.'.format(y, lati, lng))

The geograpical coordinate of Birmingham are 33.52068000000003, -86.81175999999994.


#### Creating a map of the selected city with different venues superimposed on top with there unique venue number and colour.

In [36]:
# create map
map_y = folium.Map(location=[lati, lng], zoom_start=11)

# set color scheme for the clusters
xlength = len(x_data['VenueCategory'].unique())
a = np.arange(xlength)
bc = [i + a + (i*a)**2 for i in range(xlength)]
colors_array = iter(cm.rainbow(np.linspace(0, 1, len(bc))))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# drawing radius of search
folium.Circle(location=[lati,lng],radius=radius,color='green',opacity=0.5,fill=True,fill_color='blue').add_to(map_y)

# add markers to the map
markers_colors = []

for lat, lon, cate, nos, city in zip(sortedx.VenueLatitude, sortedx.VenueLongitude, sortedx.VenueCategory, sortedx.VenueNumber, sortedx.Neighborhood):
    label = 'Category:{}, Category No.:{}, City:{}'.format(cate, nos, city)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[nos-1],
        fill=True,
        fill_opacity=1,
        fill_color=rainbow[nos-1]).add_to(map_y)
       
map_y

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting the common kind of cities in a particular state.

In first step we have collected the required **data: dataframe containing list of all 50 states and their cities. We have also **identified top venues** (according to Foursquare categorization).

Second step in our analysis will be exploration of '**top venues**' across different cities of the selected state - we will use **folium** for creating maps of all the top venues in the vicinity.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than five similar venues in radius of 9.3 Miles**, and we will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

#### Analyze each neighboring city.

In [18]:
# one hot encoding
y_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
y_onehot['Neighborhoods'] = venues_df['Neighborhood']

# move neighborhood column to the first column
fixed_columns = [y_onehot.columns[-1]] + list(y_onehot.columns[:-1])
y_onehot = y_onehot[fixed_columns]

print(y_onehot.shape)
y_onehot.head()

(2687, 218)


Neighborhoods  ATM  Accessories Store  Airport  Airport Terminal  \
0  Alexander City    0                  0        0                 0   
1  Alexander City    0                  0        0                 0   
2  Alexander City    0                  0        0                 0   
3  Alexander City    0                  0        0                 0   
4  Alexander City    0                  0        0                 0   

   American Restaurant  Antique Shop  Arcade  Art Museum  Arts & Crafts Store  \
0                    1             0       0           0                    0   
1                    0             0       0           0                    0   
2                    1             0       0           0                    0   
3                    0             0       0           0                    0   
4                    0             0       0           0                    0   

   Asian Restaurant  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                 0            0          0           0       0     0    0   
1                 0            0          0           0       0     0    0   
2                 0            0          0           0       0     0    0   
3                 0            0          0           0       0     0    0   
4                 0            0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beer Bar  \
0               0                 0                   0         0   
1               0                 0                   0         0   
2               0                 0                   0         0   
3               0                 0                   0         0   
4               0                 0                   0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Trail  Bistro  Boat or Ferry  \
0            0           0              0           0       0              0   
1            0           0              0           0       0              0   
2            0           0              0           0       0              0   
3            0           0              0           0       0              0   
4            0           0              0           0       0              0   

   Bookstore  Border Crossing  Botanical Garden  Bowling Alley  \
0          0                0                 0              0   
1          0                0                 0              0   
2          0                0                 0              0   
3          0                0                 0              0   
4          0                0                 0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  Buffet  \
0                     0               0        0       0       0   
1                     0               0        0       0       0   
2                     0               0        0       0       0   
3                     0               0        0       0       0   
4                     0               0        0       0       0   

   Burger Joint  Bus Station  Business Service  Café  \
0             0            0                 0     0   
1             0            0                 0     0   
2             0            0                 0     0   
3             0            0                 0     0   
4             0            0                 0     0   

   Cajun / Creole Restaurant  Campground  Caribbean Restaurant  Casino  Cave  \
0                          0           0                     0       0     0   
1                          0           0                     0       0     0   
2                          0           0                     0       0     0   
3                          0           1                     0       0     0   
4                          0           0                     0       0     0   

   Cheese Shop  Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0            0

#### Next, let's group rows by neighboring city and by taking the mean of the frequency of occurrence of each category.

In [19]:
y_grouped = y_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(y_grouped.shape)
y_grouped

(39, 218)


Neighborhoods       ATM  Accessories Store   Airport  Airport Terminal  \
0   Alexander City  0.027027           0.000000  0.000000          0.000000   
1        Andalusia  0.000000           0.000000  0.000000          0.026316   
2         Anniston  0.000000           0.014286  0.000000          0.000000   
3           Athens  0.000000           0.000000  0.000000          0.000000   
4           Atmore  0.000000           0.000000  0.000000          0.000000   
5           Auburn  0.000000           0.000000  0.000000          0.000000   
6         Bessemer  0.000000           0.000000  0.000000          0.000000   
7       Birmingham  0.000000           0.000000  0.000000          0.000000   
8        Chickasaw  0.000000           0.000000  0.000000          0.000000   
9          Clanton  0.000000           0.000000  0.000000          0.000000   
10         Cullman  0.000000           0.000000  0.000000          0.000000   
11         Decatur  0.000000           0.000000  0.000000          0.000000   
12       Demopolis  0.000000           0.000000  0.043478          0.000000   
13          Dothan  0.000000           0.000000  0.000000          0.000000   
14      Enterprise  0.000000           0.000000  0.022222          0.000000   
15         Eufaula  0.000000           0.000000  0.000000          0.000000   
16        Florence  0.000000           0.000000  0.000000          0.000000   
17      Fort Payne  0.000000           0.000000  0.000000          0.000000   
18         Gadsden  0.000000           0.000000  0.000000          0.000000   
19      Greenville  0.000000           0.000000  0.000000          0.000000   
20    Guntersville  0.000000           0.000000  0.000000          0.000000   
21      Huntsville  0.000000           0.000000  0.000000          0.000000   
22          Jasper  0.000000           0.000000  0.000000          0.000000   
23          Marion  0.000000           0.000000  0.000000          0.000000   
24          Mobile  0.000000           0.000000  0.000000          0.000000   
25      Montgomery  0.000000           0.000000  0.000000          0.000000   
26         Opelika  0.000000           0.000000  0.000000          0.000000   
27           Ozark  0.000000           0.000000  0.050000          0.000000   
28     Phenix City  0.000000           0.000000  0.000000          0.000000   
29        Prichard  0.000000           0.000000  0.000000          0.000000   
30      Scottsboro  0.000000           0.000000  0.000000          0.000000   
31           Selma  0.000000           0.000000  0.000000          0.000000   
32       Sheffield  0.000000           0.000000  0.000000          0.000000   
33       Sylacauga  0.000000           0.000000  0.000000          0.000000   
34       Talladega  0.000000           0.000000  0.000000          0.000000   
35            Troy  0.000000           0.000000  0.000000          0.000000   
36      Tuscaloosa  0.000000           0.000000  0.000000          0.000000   
37       Tuscumbia  0.000000           0.000000  0.000000          0.000000   
38        Tuskegee  0.000000           0.000000  0.000000          0.000000   

    American Restaurant  Antique Shop  Arcade  Art Museum  \
0              0.108108      0.000000    0.00        0.00   
1              0.052632      0.000000    0.00        0.00   
2              0.014286      0.000000    0.00        0.00   
3              0.067797      0.016949    0.00        0.00   
4              0.054054      0.000000    0.00        0.00   
5              0.070000      0.000000    0.00        0.00   
6              0.040000      0.000000    0.00        0.00   
7              0.040000      0.000000    0.00        0.01   
8              0.030000      0.000000    0.00        0.01   
9              0.020833      0.000000    0.00        0.00   
10             0.050000      0.000000    0.00        0.00   
11             0.015152      0.000000    0.00        0.00   
12             0.000000      0.000000    0.00      

## Here we can check percentage existance of any particular category of venue in all the cities of the selected state.

In [20]:
len(y_grouped[y_grouped["Seafood Restaurant"] > 0])

34

In [21]:
y_seafood = y_grouped[["Neighborhoods","Seafood Restaurant"]]
y_seafood.head()

Neighborhoods  Seafood Restaurant
0  Alexander City            0.027027
1       Andalusia            0.026316
2        Anniston            0.014286
3          Athens            0.033898
4          Atmore            0.027027

#### Let's print each neighboring city along with the top 5 most common venues.

In [23]:
num_top_venues = 5

for hood in y_grouped['Neighborhoods']:
    print("----"+hood+"----")
    temp = y_grouped[y_grouped['Neighborhoods'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Alexander City----
                  venue  freq
0   American Restaurant  0.11
1  Fast Food Restaurant  0.11
2           Gas Station  0.08
3         Grocery Store  0.08
4           Pizza Place  0.05


----Andalusia----
                  venue  freq
0        Discount Store  0.13
1  Fast Food Restaurant  0.11
2              Pharmacy  0.08
3        Sandwich Place  0.08
4   American Restaurant  0.05


----Anniston----
                  venue  freq
0  Fast Food Restaurant  0.07
1        Discount Store  0.06
2              Pharmacy  0.04
3          Burger Joint  0.04
4           Gas Station  0.04


----Athens----
                  venue  freq
0        Discount Store  0.19
1  Fast Food Restaurant  0.07
2   American Restaurant  0.07
3    Mexican Restaurant  0.05
4         Grocery Store  0.05


----Atmore----
                  venue  freq
0  Fast Food Restaurant  0.16
1         Grocery Store  0.08
2                 Hotel  0.05
3   Fried Chicken Joint  0.05
4          Intersection  0.05


--

### Let's put that into a _pandas_ dataframe.

#### First, let's write a function to sort the venues in descending order.

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#### Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [25]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhoods']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhoods'] = y_grouped['Neighborhoods']

for ind in np.arange(y_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(y_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhoods 1st Most Common Venue 2nd Most Common Venue  \
0  Alexander City   American Restaurant  Fast Food Restaurant   
1       Andalusia        Discount Store  Fast Food Restaurant   
2        Anniston  Fast Food Restaurant        Discount Store   
3          Athens        Discount Store  Fast Food Restaurant   
4          Atmore  Fast Food Restaurant         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Gas Station         Grocery Store           Pizza Place   
1              Pharmacy        Sandwich Place   American Restaurant   
2              Pharmacy          Burger Joint           Gas Station   
3   American Restaurant    Mexican Restaurant         Grocery Store   
4                 Hotel   Fried Chicken Joint          Intersection   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Discount Store   Fried Chicken Joint                   ATM   
1           Pizza Place   Fried Chicken Joint   Japanese Restaurant   
2                 Hotel         Grocery Store      Department Store   
3              Pharmacy             BBQ Joint    Seafood Restaurant   
4   American Restaurant        Discount Store        Sandwich Place   

        9th Most Common Venue 10th Most Common Venue  
0                  Campground     Mexican Restaurant  
1  Construction & Landscaping            Post Office  
2              Baseball Field         Sandwich Place  
3              Sandwich Place            Pizza Place  
4                      Buffet         Breakfast Spot

## 4. Cluster Neighborhoods

#### Run _k_-means to cluster the neighboring cities into 5 clusters according to their similarities in venues.

In [26]:
# set number of clusters
kclusters = 5

y_grouped_clustering = y_grouped.drop('Neighborhoods', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(y_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 1, 1, 1, 2, 4, 4, 4, 4, 1])

#### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighboring city.

In [27]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

y_merged = state_df

# merge y_grouped with state_df to add latitude/longitude for each neighborhood
y_merged = y_merged.join(neighborhoods_venues_sorted.set_index('Neighborhoods'), on='Neighborhood')

y_merged.head() # check the last columns!

Neighborhood  Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  Alexander City  32.93884  -85.95295               2   American Restaurant   
1       Andalusia  31.32014  -86.49449               1        Discount Store   
2        Anniston  33.65712  -85.81891               1  Fast Food Restaurant   
3          Athens  34.80450  -86.97128               1        Discount Store   
4          Atmore  31.02526  -87.49380               2  Fast Food Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Fast Food Restaurant           Gas Station         Grocery Store   
1  Fast Food Restaurant              Pharmacy        Sandwich Place   
2        Discount Store              Pharmacy          Burger Joint   
3  Fast Food Restaurant   American Restaurant    Mexican Restaurant   
4         Grocery Store                 Hotel   Fried Chicken Joint   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0           Pizza Place        Discount Store   Fried Chicken Joint   
1   American Restaurant           Pizza Place   Fried Chicken Joint   
2           Gas Station                 Hotel         Grocery Store   
3         Grocery Store              Pharmacy             BBQ Joint   
4          Intersection   American Restaurant        Discount Store   

  8th Most Common Venue       9th Most Common Venue 10th Most Common Venue  
0                   ATM                  Campground     Mexican Restaurant  
1   Japanese Restaurant  Construction & Landscaping            Post Office  
2      Department Store              Baseball Field         Sandwich Place  
3    Seafood Restaurant              Sandwich Place            Pizza Place  
4        Sandwich Place                      Buffet         Breakfast Spot

## Results and Discussion <a name="results"></a>

#### Let's visualize the clusters.

In [28]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=7)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(y_merged['Latitude'], y_merged['Longitude'], y_merged['Neighborhood'], y_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 5. Examine Clusters

#### Now, we can examine each cluster & determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, we can then assign a name to each cluster like cities with top common venues containing restaurants.

#### Cluster 1

In [29]:
y_merged.loc[y_merged['Cluster Labels'] == 0, y_merged.columns[[0] + list(range(4, y_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
12    Demopolis  Fast Food Restaurant                 Hotel   
31        Selma   Fried Chicken Joint             BBQ Joint   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
12           Pizza Place    Mexican Restaurant           Gas Station   
31                 Hotel           Pizza Place              Pharmacy   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
12        Sandwich Place   Fried Chicken Joint     Convenience Store   
31        Sandwich Place  Fast Food Restaurant           Gas Station   

   9th Most Common Venue 10th Most Common Venue  
12              Pharmacy              BBQ Joint  
31         Grocery Store       Department Store

#### Cluster 2

In [30]:
y_merged.loc[y_merged['Cluster Labels'] == 1, y_merged.columns[[0] + list(range(4, y_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1      Andalusia        Discount Store  Fast Food Restaurant   
2       Anniston  Fast Food Restaurant        Discount Store   
3         Athens        Discount Store  Fast Food Restaurant   
9        Clanton        Discount Store  Fast Food Restaurant   
10       Cullman  Fast Food Restaurant    Mexican Restaurant   
14    Enterprise        Discount Store        Sandwich Place   
15       Eufaula        Discount Store  Fast Food Restaurant   
16      Florence        Discount Store         Grocery Store   
17    Fort Payne  Fast Food Restaurant        Discount Store   
18       Gadsden  Fast Food Restaurant    Mexican Restaurant   
20  Guntersville  Fast Food Restaurant        Discount Store   
22        Jasper        Discount Store           Pizza Place   
30    Scottsboro  Fast Food Restaurant           Pizza Place   
32     Sheffield        Discount Store         Grocery Store   
33     Sylacauga  Fast Food Restaurant        Discount Store   
34     Talladega        Discount Store  Fast Food Restaurant   
35          Troy                 Hotel   Fried Chicken Joint   
37     Tuscumbia        Discount Store  Fast Food Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1               Pharmacy        Sandwich Place   American Restaurant   
2               Pharmacy          Burger Joint           Gas Station   
3    American Restaurant    Mexican Restaurant         Grocery Store   
9            Gas Station        Sandwich Place          Burger Joint   
10          Burger Joint        Sandwich Place   American Restaurant   
14           Pizza Place  Fast Food Restaurant           Coffee Shop   
15     Convenience Store        Sandwich Place   Fried Chicken Joint   
16            Steakhouse          Burger Joint    Mexican Restaurant   
17           Pizza Place           Gas Station     Convenience Store   
18        Discount Store         Grocery Store    Seafood Restaurant   
20           Pizza Place    Mexican Restaurant           Gas Station   
22   American Restaurant  Fast Food Restaurant    Mexican Restaurant   
30        Discount Store        Sandwich Place         Grocery Store   
32            Steakhouse          Burger Joint    Mexican Restaurant   
33   Fried Chicken Joint        Sandwich Place        Ice Cream Shop   
34   Fried Chicken Joint     Mobile Phone Shop     Convenience Store   
35         Grocery Store    Mexican Restaurant        Sandwich Place   
37         Grocery Store            Steakhouse    Mexican Restaurant   

   6th Most Common Venue 7th Most Common Venue  \
1            Pizza Place   Fried Chicken Joint   
2                  Hotel         Grocery Store   
3               Pharmacy             BBQ Joint   
9                  Hotel          Intersection   
10        Discount Store             BBQ Joint   
14                 Hotel                   Bar   
15    Mexican Restaurant           Gas Station   
16           Coffee Shop                Museum   
17    Mexican Restaurant        Sandwich Place   
18        Breakfast Spot   American Restaurant   
20         Grocery Store                 Hotel   
22         Grocery Store             BBQ Joint   
30                   Bar           Video Store   
32  Fast Food Restaurant           Coffee Shop   
33    Mexican Restaurant           Coffee Shop   
34           Pizza Place              Pharmacy   
35        Ice Cream Shop  Fast Food Restaurant   
37          Burger Joint           Coffee Shop   

              8th Most Common Venue       9th Most Common Venue  \
1               Japanese Restaurant  Construction & Landscaping   
2                  Department Store              Baseball Field   
3                Seafood Restaurant              Sandwich Place   
9                     Grocery Store         Fried Chicken Joint   
10                      Pizza Place         Fried Chicken Joint   
14                              Gym               Grocery Store  

#### Cluster 3

In [31]:
y_merged.loc[y_merged['Cluster Labels'] == 2, y_merged.columns[[0] + list(range(4, y_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0   Alexander City   American Restaurant  Fast Food Restaurant   
4           Atmore  Fast Food Restaurant         Grocery Store   
19      Greenville  Fast Food Restaurant        Discount Store   
27           Ozark  Fast Food Restaurant           Gas Station   
38        Tuskegee  Fast Food Restaurant             Rest Area   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Gas Station         Grocery Store           Pizza Place   
4                  Hotel   Fried Chicken Joint          Intersection   
19   American Restaurant           Gas Station        Sandwich Place   
27   Fried Chicken Joint                 Hotel               Airport   
38         Grocery Store         Historic Site                  Park   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Discount Store   Fried Chicken Joint                   ATM   
4    American Restaurant        Discount Store        Sandwich Place   
19             Rest Area              Pharmacy                 Hotel   
27           Pizza Place   American Restaurant     Food & Drink Shop   
38                Museum                Forest   American Restaurant   

   9th Most Common Venue 10th Most Common Venue  
0             Campground     Mexican Restaurant  
4                 Buffet         Breakfast Spot  
19         Grocery Store    Fried Chicken Joint  
27         Big Box Store     Mexican Restaurant  
38              Pharmacy    Fried Chicken Joint

#### Cluster 4

In [32]:
y_merged.loc[y_merged['Cluster Labels'] == 3, y_merged.columns[[0] + list(range(4, y_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
23       Marion        Discount Store                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
23  Fast Food Restaurant        Sandwich Place           Bus Station   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
23  Outdoor Supply Store                Museum           Music Venue   

   9th Most Common Venue 10th Most Common Venue  
23         National Park        Nature Preserve

#### Cluster 5

In [33]:
y_merged.loc[y_merged['Cluster Labels'] == 4, y_merged.columns[[0] + list(range(4, y_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5        Auburn   American Restaurant         Grocery Store   
6      Bessemer         Grocery Store  Fast Food Restaurant   
7    Birmingham               Brewery           Coffee Shop   
8     Chickasaw         Grocery Store           Coffee Shop   
11      Decatur             BBQ Joint            Steakhouse   
13       Dothan   American Restaurant  Fast Food Restaurant   
21   Huntsville           Coffee Shop    Mexican Restaurant   
24       Mobile    Seafood Restaurant           Coffee Shop   
25   Montgomery   American Restaurant         Grocery Store   
26      Opelika   American Restaurant        Sandwich Place   
28  Phenix City         Grocery Store             BBQ Joint   
29     Prichard         Grocery Store           Coffee Shop   
36   Tuscaloosa                   Bar           Coffee Shop   

              3rd Most Common Venue     4th Most Common Venue  \
5                         BBQ Joint            Sandwich Place   
6                    Ice Cream Shop                       Gym   
7                             Hotel  Mediterranean Restaurant   
8                Mexican Restaurant        Seafood Restaurant   
11               Italian Restaurant            Sandwich Place   
13               Mexican Restaurant             Grocery Store   
21                    Grocery Store                 BBQ Joint   
24  Southern / Soul Food Restaurant             Grocery Store   
25                      Pizza Place               Coffee Shop   
26                      Pizza Place                  Pharmacy   
28                      Coffee Shop        Mexican Restaurant   
29               Mexican Restaurant        Seafood Restaurant   
36                   Sandwich Place      Fast Food Restaurant   

              5th Most Common Venue            6th Most Common Venue  \
5                       Golf Course                      Pizza Place   
6               Fried Chicken Joint              American Restaurant   
7               American Restaurant                        BBQ Joint   
8                    Sandwich Place  Southern / Soul Food Restaurant   
11                    Grocery Store               Mexican Restaurant   
13                      Pizza Place                   Breakfast Spot   
21                          Brewery              American Restaurant   
24                           Museum                             Café   
25             Fast Food Restaurant                              Bar   
26                        BBQ Joint                    Grocery Store   
28                             Park                      Pizza Place   
29  Southern / Soul Food Restaurant                        BBQ Joint   
36               Mexican Restaurant              American Restaurant   

   7th Most Common Venue            8th Most Common Venue  \
5     Mexican Restaurant                     Burger Joint   
6     Mexican Restaurant                     Burger Joint   
7                    Bar                              Gym   
8     Italian Restaurant              American Restaurant   
11        Discount Store                         Pharmacy   
13             BBQ Joint                            Hotel   
21            Restaurant                   Science Museum   
24  Gym / Fitness Center                        BBQ Joint   
25          Burger Joint                           Bakery   
26    Mexican Restaurant               Italian Restaurant   
28     Korean Restaurant  Southern / Soul Food Restaurant   
29                   Bar               Italian Restaurant   
36           Pizza Place                            Hotel   

   9th Most Common Venue 10th Most Common Venue  
5     Italian Restaurant            Coffee Shop  
6            Coffee Shop       Video Game Store  
7                   Park              Gastropub  
8                   Café   Fast Food Restaurant  
11                  Park         Breakfast Spot  
13      Department Store             Steakhou

Our analysis shows that although there is a great number of restaurants in Berlin (~2000 in our initial area of interest which was 12x12km around Alexanderplatz), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north and west from Alexanderplatz, so we focused our attention to areas south, south-east and east, corresponding to boroughs Kreuzberg, Friedrichshain and south-east corner of central Mitte borough. Another borough was identified as potentially interesting (Prenzlauer Berg, north-east from Alexanderplatz), but our attention was focused on Kreuzberg and Friedrichshain which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from Alexanderplatz) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Berlin center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Berlin areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Kreuzberg and Friedrichshain), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.